In [99]:
import pandas as pd 
import h2o 
import numpy as np
import h2o.automl as H2OAutoML
import matplotlib.pyplot as plt
import datetime
from sklearn.metrics import classification_report
from sklearn.metrics import confusion_matrix
import plotly
import torch
from neuralprophet import NeuralProphet
import plotly.graph_objects as go

### Define Functions to use later

In [100]:
def left(s, amount):
    return s[:-amount]
def right(s, amount):
    return s[-amount:]
def season_of_date(date):
    year = str(date.year)
    seasons = {'spring': pd.date_range(start='21/03/'+year, end='20/06/'+year),
               'summer': pd.date_range(start='21/06/'+year, end='22/09/'+year),
               'autumn': pd.date_range(start='23/09/'+year, end='20/12/'+year)}
    if date in seasons['spring']:
        return 'Spring'
    if date in seasons['summer']:
        return 'Summer'
    if date in seasons['autumn']:
        return 'Autumn'
    else:
        return 'Winter'

In [101]:
pop_df = pd.read_csv("Population Data.csv")
temp_df = pd.read_csv("Temperature Data.csv")

In [102]:
temp_df_group = temp_df.groupby(['location_date','station_code']).mean().unstack().reset_index()

In [103]:
temp_df_group = temp_df_group.assign(location_date = pd.to_datetime(temp_df_group.location_date))

In [104]:
temp_df_group.columns = ['_'.join(tup).rstrip('_') for tup in temp_df_group.columns.values]
temp_df_group = temp_df_group.set_index('location_date')
temp_df_group = temp_df_group.rename(columns = {'location_date':'ds'})

In [105]:
temp_df_group = temp_df_group.sort_index()

In [106]:
temp_df_group.head()

temp_mean_c_KALB  temp_mean_c_KATL  temp_mean_c_KBDL  \
location_date                                                         
2015-01-01            -3.362500          6.758333         -1.991667   
2015-01-02            -0.683333          8.116667          0.466667   
2015-01-03            -3.545833         11.154167         -2.258333   
2015-01-04             4.166667         14.279167          1.754167   
2015-01-05            -4.654167          5.045833         -1.429167   

               temp_mean_c_KBNA  temp_mean_c_KBOI  temp_mean_c_KBOS  \
location_date                                                         
2015-01-01             1.141667        -11.070833         -2.329167   
2015-01-02             5.037500         -9.750000          1.666667   
2015-01-03            13.745833         -7.662500         -1.841667   
2015-01-04             7.945833         -4.029167          5.537500   
2015-01-05            -2.954167         -0.125000          0.004167   

               temp_mean_c_KBUF  temp_mean_c_KBUR  temp_mean_c_KBWI  \
location_date                                                         
2015-01-01            -3.254167          6.391667         -0.345833   
2015-01-02            -1.587500          7.687500          2.216667   
2015-01-03            -0.633333          8.804167          1.633333   
2015-01-04             5.541667         11.550000         10.079167   
2015-01-05            -9.812500         15.575000          1.704167   

               temp_mean_c_KCMH  ...  temp_max_c_KPHX  temp_max_c_KPIT  \
location_date                    ...                                     
2015-01-01            -2.541667  ...              7.2              1.7   
2015-01-02            -0.558333  ...             11.7              2.2   
2015-01-03             5.958333  ...             12.2             14.4   
2015-01-04             6.716667  ...             17.8             15.6   
2015-01-05            -8.950000  ...             23.3             -1.1   

               temp_max_c_KPWM  temp_max_c_KRDU  temp_max_c_KRIC  \
location_date                                                      
2015-01-01                -0.6             10.6              9.4   
2015-01-02                 3.3             12.2             11.1   
2015-01-03                 1.1             10.6              8.9   
2015-01-04                 1.7             19.4             20.6   
2015-01-05                 5.0             11.7             11.7   

               temp_max_c_KSAC  temp_max_c_KSEA  temp_max_c_KSFO  \
location_date                                                      
2015-01-01                10.6              5.0             12.2   
2015-01-02                11.1              5.0             11.1   
2015-01-03                12.2              4.4             11.7   
2015-01-04                13.9             10.6             12.2   
2015-01-05                13.9             12.2             15.0   

               temp_max_c_KSLC  temp_max_c_KSTL  
location_date                                    
2015-01-01                -5.0              4.4  
2015-01-02                -3.3              4.4  
2015-01-03                 0.0              6.0  
2015-01-04                 1.1              4.0  
2015-01-05                 5.6             -3.3  

[5 rows x 117 columns]

Fix missing data with rolling window

In [107]:
temp_df_group_rolled = temp_df_group.fillna(temp_df_group.rolling(window = 14, min_periods=1).mean())

In [108]:
no_nan_temp_df = temp_df_group_rolled.copy(deep=True)

In [109]:
stacked_df = no_nan_temp_df.stack().reset_index()

In [110]:
nan_df = temp_df_group[pd.isnull(temp_df_group).any(axis=1)].fillna(-100).stack().reset_index()
nan_df = nan_df[nan_df[0] == -100]

In [111]:
stacked_df['station_code'] = stacked_df.level_1.apply(lambda x: right(x,4))
stacked_df['level_1'] = stacked_df.level_1.apply(lambda x: left(x,5))
nan_df['station_code'] = nan_df.level_1.apply(lambda x: right(x,4))
nan_df['level_1'] = nan_df.level_1.apply(lambda x: left(x,5))

In [112]:
stacked_df = stacked_df.groupby(['location_date','station_code','level_1']).sum().unstack()
nan_df = nan_df.groupby(['location_date','station_code','level_1']).sum().unstack()

In [113]:
stacked_df.columns = list(stacked_df.columns.levels[1])
nan_df.columns = list(nan_df.columns.levels[1])

In [114]:
stacked_df = stacked_df.reset_index()
nan_df = nan_df.reset_index()

In [115]:
stacked_df_nan = stacked_df.merge(nan_df[['location_date','station_code','temp_mean_c']]
                 , how = 'left', left_on= ['location_date','station_code'] , right_on = ['location_date', 'station_code'])

In [116]:
stacked_df_nan = stacked_df_nan.assign(projected = np.where(pd.isnull(stacked_df_nan.temp_mean_c_y) == True,0,1))

In [117]:
stacked_df = stacked_df_nan.drop('temp_mean_c_y', axis = 1).rename(columns = {'temp_mean_c_x':'temp_mean_c'})

## Combining Cities and Weather Stations 

In [118]:
weather_stations = temp_df[['name','station_code']].drop_duplicates().reset_index(drop=True)

In [119]:
weather_stations['join'] = 1
pop_df['join'] = 1

In [120]:
df_full = weather_stations.merge(pop_df).drop('join',axis =1)
df_full['name_2'] = df_full.name.apply(lambda x: str(x))

In [121]:
weather_stations.drop('join',axis=1, inplace=True) 
pop_df.drop('join',axis=1, inplace=True) 

In [122]:
df_full['match'] = df_full.apply(lambda x: x.City in x.name_2, axis = 1)

In [123]:
df_full = df_full[df_full['match']==True].drop([2416,8852,9339]).drop(['name_2'
                            ,'match'],axis = 1).merge(weather_stations,how='right')

In [124]:
df_full.loc[1] = ['Windsor Locks','KBDL','Hartford','Connecticut',124867,-72.6833,41.766]
df_full.loc[10] = ['Covington','KCVG','Cincinnati','Ohio',296223,-84.5064,39.1399]
df_full.loc[17] = ['Wash DC/Dulles','KIAD','Washington','District of Columbia',617996,-77.0171,38.9041]
df_full.loc[20] = ['NYC/LaGuardia','KLGA','New York','New York',8244910,-73.9385,40.6643]
df_full.loc[37] = ['St Louis/Lambert','KSTL','St. Louis','Missouri',318069,-90.2446,38.6357]
df_full.loc[38] = ['Albany','KALB','Yonkers','New York',197399,-73.8674,40.9459]

In [125]:
pop_df['join'] = 1
df_full['join'] = 1

In [126]:
df_full_pop = df_full.merge(pop_df, left_on = 'join' , right_on = 'join').drop('join',axis =1)

In [127]:
df_full_pop = df_full_pop.assign(pythag = (df_full_pop.Lon_x - df_full_pop.Lon_y)**2 
                                 + (df_full_pop.Lat_x - df_full_pop.Lat_y)**2)

In [128]:
df_full_pop['rank'] = df_full_pop.sort_values(['City_y','pythag'], ascending=[True,True]) \
             .groupby(['City_y','State_y']) \
             .cumcount() 

In [129]:
new_pop_df = df_full_pop[df_full_pop['rank']==0][['City_y','State_y','population_y','Lon_y','Lat_y','station_code','name']].rename(columns={
    'City_y':'City','State_y':'State','population_y':'population','Lon_y':'Lon','Lat_y':'Lat'})

## Formatting data together for plots

In [130]:
stacked_df = stacked_df.assign(season = stacked_df.location_date.apply(lambda x: season_of_date(x)))
stacked_df = stacked_df.assign(month = stacked_df.location_date.apply(lambda x: 
                                    datetime.datetime.strptime(str(x.month), "%m").strftime("%B")))

In [131]:
stacked_df = stacked_df.assign(year = stacked_df.location_date.apply(lambda x: x.year))

In [132]:
full = new_pop_df.merge(stacked_df)

In [133]:
full = full.assign(temp_pop_mean = full.temp_mean_c * full.population)

In [134]:
full_agg = full.groupby(['location_date','year','season','month']).sum()[['temp_pop_mean','population']]

In [135]:
full_agg = full_agg.assign(temp_mean_avg = full_agg.temp_pop_mean / full_agg.population)

In [136]:
full_agg = full_agg.drop(['temp_pop_mean','population'],axis = 1).reset_index()

In [137]:
full_agg = full_agg.merge(full.groupby('location_date',as_index =False).min()[['location_date'
                            ,'temp_min_c']]).merge(full.groupby('location_date',as_index =False).max()[['location_date'
                            ,'temp_max_c']]).merge(full.groupby('location_date',as_index =False).sum()[['location_date'
                            ,'projected']])

In [138]:
full_agg = full_agg.merge(full.groupby(['year','season'],as_index =False).min()[['year','season'
            ,'temp_min_c']].rename(columns = {'temp_min_c':'temp_min_season'})).merge(full.groupby(['year'
            ,'season'],as_index =False).max()[['year','season','temp_max_c']].rename(columns = {'temp_max_c'
            :'temp_max_season'})).merge(full.groupby(['year','season'],as_index =False).mean()[['year','season'
            ,'temp_mean_c']].rename(columns = {'temp_mean_c':'temp_mean_season'}))

In [139]:
full_agg = full_agg.merge(full.groupby(['year','month'],as_index =False).min()[['year','month'
            ,'temp_min_c']].rename(columns = {'temp_min_c':'temp_min_month'})).merge(full.groupby(['year'
            ,'month'],as_index =False).max()[['year','month','temp_max_c']].rename(columns = {'temp_max_c'
            :'temp_max_month'})).merge(full.groupby(['year','month'],as_index =False).mean()[['year','month'
            ,'temp_mean_c']].rename(columns = {'temp_mean_c':'temp_mean_month'}))

In [140]:
full_agg = full_agg.sort_values('location_date')

In [141]:
full_agg

location_date  year  season    month  temp_mean_avg  temp_min_c  \
0       2015-01-01  2015  Winter  January       2.326470       -14.4   
1       2015-01-02  2015  Winter  January       4.392856       -13.9   
2       2015-01-03  2015  Winter  January       5.544732       -20.0   
3       2015-01-04  2015  Winter  January       6.215924       -22.8   
4       2015-01-05  2015  Winter  January       3.405179       -23.9   
...            ...   ...     ...      ...            ...         ...   
2297    2021-04-16  2021  Spring    April      12.612207        -2.8   
2298    2021-04-17  2021  Spring    April      13.122358        -1.1   
2299    2021-04-18  2021  Spring    April      15.222492        -0.6   
2300    2021-04-19  2021  Spring    April      15.007311        -6.1   
2301    2021-04-20  2021  Spring    April      14.090206        -8.3   

      temp_max_c  projected  temp_min_season  temp_max_season  \
0           15.0          0            -23.9             32.8   
1           24.4          0            -23.9             32.8   
2           25.0          0            -23.9             32.8   
3           21.1          0            -23.9             32.8   
4           26.7          0            -23.9             32.8   
...          ...        ...              ...              ...   
2297        28.3          0             -8.3             36.1   
2298        31.1          0             -8.3             36.1   
2299        32.2          0             -8.3             36.1   
2300        31.1          0             -8.3             36.1   
2301        32.8          4             -8.3             36.1   

      temp_mean_season  temp_min_month  temp_max_month  temp_mean_month  
0             7.023639           -23.9            28.9         5.560351  
1             7.023639           -23.9            28.9         5.560351  
2             7.023639           -23.9            28.9         5.560351  
3             7.023639           -23.9            28.9         5.560351  
4             7.023639           -23.9            28.9         5.560351  
...                ...             ...             ...              ...  
2297         14.468570            -8.3            36.1        14.793495  
2298         14.468570            -8.3            36.1        14.793495  
2299         14.468570            -8.3            36.1        14.793495  
2300         14.468570            -8.3            36.1        14.793495  
2301         14.468570            -8.3            36.1        14.793495  

[2302 rows x 14 columns]

In [142]:
for i in range(len(full_agg)):
    full_agg.loc[i,'text_min'] = """
    Date : {} <br>
    Min Temp °C : {} <br>
    Season : {}<br>
    Month : {} <br>
    Season Min Temp °C : {} <br>
    Month Min Temp °C : {} <br>
    Number of Projected Readings : {}""".format(full_agg.location_date[i].strftime('%b %d, %Y'),
                                                full_agg.temp_min_c[i],
                                                full_agg.season[i],
                                                full_agg.month[i],
                                                full_agg.temp_min_season[i],
                                                full_agg.temp_min_month[i],
                                                full_agg.projected[i])
    full_agg.loc[i,'text_max'] = """
    Date : {} <br>
    Max Temp °C : {} <br>
    Season : {}<br>
    Month : {} <br>
    Season Max Temp °C : {} <br>
    Month Max Temp °C : {} <br>
    Number of Projected Readings : {}""".format(full_agg.location_date[i].strftime('%b %d, %Y'),
                                                full_agg.temp_max_c[i],
                                                full_agg.season[i],
                                                full_agg.month[i],
                                                full_agg.temp_max_season[i],
                                                full_agg.temp_max_month[i],
                                                full_agg.projected[i])
    full_agg.loc[i,'text_mean'] = """
    Date : {} <br>
    Mean Temp °C : {} <br>
    Season : {}<br>
    Month : {} <br>
    Season Mean Temp °C : {} <br>
    Month Mean Temp °C : {} <br>
    Number of Projected Readings : {}""".format(full_agg.location_date[i].strftime('%b %d, %Y'),
                                                round(full_agg.temp_mean_avg[i],1),
                                                full_agg.season[i],
                                                full_agg.month[i],
                                                round(full_agg.temp_mean_season[i],1),
                                                round(full_agg.temp_mean_month[i],1),
                                                full_agg.projected[i])

# Main Graph

In [143]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=full_agg.location_date, y=full_agg.temp_min_c, name="US Min Temp",
                         line_color='deepskyblue',hoverinfo ='text', text = full_agg.text_min))

fig.add_trace(go.Scatter(x=full_agg.location_date, y=full_agg.temp_max_c, name="US Max Temp",
                         line_color='salmon', hoverinfo ='text' , text = full_agg.text_max))

fig.add_trace(go.Scatter(x=full_agg.location_date, y=full_agg.temp_mean_avg, name="US Mean Temp",
                         line_color='dimgray', hoverinfo ='text' , text = full_agg.text_mean))
fig.update_layout(title_text='Temperature for US Cities <br> (Hover for City Info)',
                  xaxis_rangeslider_visible=True,
                  uniformtext_mode='hide',
                  xaxis=dict(title='Date'),
                  yaxis=dict(title='Temp °C'))

fig.update_layout(
    updatemenus=[
        dict(
            active=-1,
            buttons=list([
                dict(label="Min Only",
                     method="update",
                     args=[{"visible": [True,False,False]},
                           {"title": "Temperature for US Cities (Min Only) <br> (Hover for City Info)"}]),
                dict(label="Max Only",
                     method="update",
                     args=[{"visible": [False,True,False]},
                           {"title": "Temperature for US Cities (Max Only) <br> (Hover for City Info)"}]),
                dict(label="Mean only",
                     method="update",
                     args=[{"visible": [False,False,True]},
                           {"title": "Seasonal Temperature for US Cities (Mean Only) <br> (Hover for City Info)"}]),
                dict(label="All",
                     method="update",
                     args=[{"visible": [True,True,True]},
                           {"title": "Seasonal Temperature for US Cities (All)<br> (Hover for City Info)"}]),
            ]),
        )
    ])
html1 = fig.to_html()
fig.show()

# Additional Graphs 

In [144]:
max_season = full.groupby(['City','State','Lon','Lat','station_code','season']).agg(func={'temp_max_c':'max'
                        ,'temp_min_c':'min','temp_mean_c':'mean'})['temp_max_c'].unstack().reset_index()
min_season = full.groupby(['City','State','Lon','Lat','station_code','season']).agg(func={'temp_max_c':'max'
                        ,'temp_min_c':'min','temp_mean_c':'mean'})['temp_max_c'].unstack().reset_index()
min_season = full.groupby(['City','State','Lon','Lat','station_code','season']).agg(func={'temp_max_c':'max'
                        ,'temp_min_c':'min','temp_mean_c':'mean'})['temp_max_c'].unstack().reset_index()

In [145]:
ts = full.groupby(['City','State','Lon','Lat','station_code','season']).agg(func={'temp_max_c':'max'
                        ,'temp_min_c':'min','temp_mean_c':'mean'}).reset_index()

In [146]:
for i in range(len(ts)):
    ts.loc[i,'text'] = """
    Long , Lat = ({},{}) <br>
    Weather Station : {} <br>
    City : {} <br>
    State : {} <br>
    Season : {} <br>
    Max Temp °C : {} <br>
    Min Temp °C : {} <br>
    Mean Temp °C : {}""".format(ts.Lon[i],ts.Lat[i],ts.station_code[i],ts.City[i]
                                ,ts.State[i],ts.season[i],ts.temp_max_c[i],ts.temp_min_c[i],round(ts.temp_mean_c[i],1))

In [147]:
ts_m = full.groupby(['City','State','Lon','Lat','station_code','month']).agg(func={'temp_max_c':'max'
                        ,'temp_min_c':'min','temp_mean_c':'mean'}).reset_index()

In [148]:
for i in range(len(ts_m)):
    ts_m.loc[i,'text'] = """
    Long , Lat = ({},{}) <br>
    Weather Station : {}<br>
    City : {}<br>
    State : {}<br>
    Month : {}<br>
    Max Temp °C : {}<br>
    Min Temp °C : {}<br>
    Mean Temp °C : {}""".format(ts_m.Lon[i],ts_m.Lat[i],ts_m.station_code[i],ts_m.City[i],ts_m.State[i]
                                ,ts_m.month[i],ts_m.temp_max_c[i],ts_m.temp_min_c[i],ts_m.temp_mean_c[i])

## Seasonal Geographic Map

In [149]:
ts_w  = ts[ts['season']=='Winter'].reset_index(drop=True)
ts_su = ts[ts['season']=='Summer'].reset_index(drop=True)
ts_sp = ts[ts['season']=='Spring'].reset_index(drop=True)
ts_a = ts[ts['season']=='Autumn'].reset_index(drop=True)


fig = go.Figure()

fig.add_trace(go.Scattergeo(
        lon = ts_sp['Lon'],
        lat = ts_sp['Lat'],
        text = ts_sp['text'],
        mode = 'markers',
        marker_color = ts_sp.index,
        showlegend=False,
        hoverinfo ='text' 
        ))
fig.add_trace(go.Scattergeo(
        lon = ts_su['Lon'],
        lat = ts_su['Lat'],
        text = ts_su['text'],
        mode = 'markers',
        marker_color = ts_su.index,
        showlegend=False,
        hoverinfo ='text' 
        ))
fig.add_trace(go.Scattergeo(
        lon = ts_a['Lon'],
        lat = ts_a['Lat'],
        text = ts_a['text'],
        mode = 'markers',
        marker_color = ts_a.index,
        showlegend=False,
        hoverinfo ='text' 
        ))
fig.add_trace(go.Scattergeo(
        lon = ts_w['Lon'],
        lat = ts_w['Lat'],
        text = ts_w['text'],
        mode = 'markers',
        marker_color = ts_w.index,
        showlegend=False,
        hoverinfo ='text' 
        ))                            

              
fig.update_layout(
        title = 'Seasonal Temperature for US Cities <br> (Hover for City Info)',
        geo_scope='usa',
    )


fig.update_layout(
    updatemenus=[
        dict(
            active=-1,
            buttons=list([
                dict(label="Spring",
                     method="update",
                     args=[{"visible": [True,False,False,False]},
                           {"title": "Seasonal Temperature for US Cities (Spring) <br> (Hover for City Info)"}]),
                dict(label="Summer",
                     method="update",
                     args=[{"visible": [False,True,False,False]},
                           {"title": "Seasonal Temperature for US Cities (Summer) <br> (Hover for City Info)"}]),
                dict(label="Autumn",
                     method="update",
                     args=[{"visible": [False,False,True,False]},
                           {"title": "Seasonal Temperature for US Cities (Autumn) <br> (Hover for City Info)"}]),
                dict(label="Winter",
                     method="update",
                     args=[{"visible": [False,False,False,True]},
                           {"title": "Seasonal Temperature for US Cities (Winter)<br> (Hover for City Info)"}]),
            ]),
        )
    ])

fig.update_layout(
        title = 'Seasonal Temperature for US Cities <br> (Hover for City Info)',
        geo_scope='usa',
    )

html2 = fig.to_html()
fig.show()

## Monthly Geographic Map

In [150]:
ts_jan  = ts_m[ts_m['month']=='January'].reset_index(drop=True)
ts_feb  = ts_m[ts_m['month']=='February'].reset_index(drop=True)
ts_mar  = ts_m[ts_m['month']=='March'].reset_index(drop=True)
ts_apr  = ts_m[ts_m['month']=='April'].reset_index(drop=True)
ts_may  = ts_m[ts_m['month']=='May'].reset_index(drop=True)
ts_jun  = ts_m[ts_m['month']=='June'].reset_index(drop=True)
ts_jul  = ts_m[ts_m['month']=='July'].reset_index(drop=True)
ts_aug  = ts_m[ts_m['month']=='August'].reset_index(drop=True)
ts_sep  = ts_m[ts_m['month']=='September'].reset_index(drop=True)
ts_oct  = ts_m[ts_m['month']=='October'].reset_index(drop=True)
ts_nov  = ts_m[ts_m['month']=='November'].reset_index(drop=True)
ts_dec  = ts_m[ts_m['month']=='December'].reset_index(drop=True)
fig = go.Figure()

fig.add_trace(go.Scattergeo(
        lon = ts_jan['Lon'],
        lat = ts_jan['Lat'],
        text = ts_jan['text'],
        mode = 'markers',
        marker_color = ts_jan.index,
        showlegend=False,
        hoverinfo ='text'
        ))
fig.add_trace(go.Scattergeo(
        lon = ts_feb['Lon'],
        lat = ts_feb['Lat'],
        text = ts_feb['text'],
        mode = 'markers',
        marker_color = ts_feb.index,
        showlegend=False,
        hoverinfo ='text'
        ))
fig.add_trace(go.Scattergeo(
        lon = ts_mar['Lon'],
        lat = ts_mar['Lat'],
        text = ts_mar['text'],
        mode = 'markers',
        marker_color = ts_mar.index,
        showlegend=False,
        hoverinfo ='text'
        ))
fig.add_trace(go.Scattergeo(
        lon = ts_apr['Lon'],
        lat = ts_apr['Lat'],
        text = ts_apr['text'],
        mode = 'markers',
        marker_color = ts_apr.index,
        showlegend=False,
        hoverinfo ='text'
        ))                            
fig.add_trace(go.Scattergeo(
        lon = ts_may['Lon'],
        lat = ts_may['Lat'],
        text = ts_may['text'],
        mode = 'markers',
        marker_color = ts_may.index,
        showlegend=False,
        hoverinfo ='text'
        ))
fig.add_trace(go.Scattergeo(
        lon = ts_jun['Lon'],
        lat = ts_jun['Lat'],
        text = ts_jun['text'],
        mode = 'markers',
        marker_color = ts_jun.index,
        showlegend=False,
        hoverinfo ='text'
        ))
fig.add_trace(go.Scattergeo(
        lon = ts_jul['Lon'],
        lat = ts_jul['Lat'],
        text = ts_jul['text'],
        mode = 'markers',
        marker_color = ts_jul.index,
        showlegend=False,
        hoverinfo ='text'
        ))
fig.add_trace(go.Scattergeo(
        lon = ts_aug['Lon'],
        lat = ts_aug['Lat'],
        text = ts_aug['text'],
        mode = 'markers',
        marker_color = ts_aug.index,
        showlegend=False,
        hoverinfo ='text'
        ))     
fig.add_trace(go.Scattergeo(
        lon = ts_sep['Lon'],
        lat = ts_sep['Lat'],
        text = ts_sep['text'],
        mode = 'markers',
        marker_color = ts_sep.index,
        showlegend=False,
        hoverinfo ='text'
        ))
fig.add_trace(go.Scattergeo(
        lon = ts_oct['Lon'],
        lat = ts_oct['Lat'],
        text = ts_oct['text'],
        mode = 'markers',
        marker_color = ts_oct.index,
        showlegend=False,
        hoverinfo ='text'
        ))
fig.add_trace(go.Scattergeo(
        lon = ts_nov['Lon'],
        lat = ts_nov['Lat'],
        text = ts_nov['text'],
        mode = 'markers',
        marker_color = ts_nov.index,
        showlegend=False,
        hoverinfo ='text'
        ))
fig.add_trace(go.Scattergeo(
        lon = ts_dec['Lon'],
        lat = ts_dec['Lat'],
        text = ts_dec['text'],
        mode = 'markers',
        marker_color = ts_dec.index,
        showlegend=False,
        hoverinfo ='text'
        ))                 
fig.update_layout(
        title = 'Seasonal Temperature for US Cities <br> (Hover for City Info)',
        geo_scope='usa',
    )


fig.update_layout(
    updatemenus=[
        dict(
            active=-1,
            buttons=list([
                dict(label="January",
                     method="update",
                     args=[{"visible": [True,False,False,False,False,False,False,False,False,False,False,False]},
                           {"title": "Seasonal Temperature for US Cities (January) <br> (Hover for City Info)"}]),
                dict(label="Feburary",
                     method="update",
                     args=[{"visible": [False,True,False,False,False,False,False,False,False,False,False,False]},
                           {"title": "Seasonal Temperature for US Cities (Feburary) <br> (Hover for City Info)"}]),
                dict(label="March",
                     method="update",
                     args=[{"visible": [False,False,True,False,False,False,False,False,False,False,False,False]},
                           {"title": "Seasonal Temperature for US Cities (March) <br> (Hover for City Info)"}]),
                dict(label="April",
                     method="update",
                     args=[{"visible": [False,False,False,True,False,False,False,False,False,False,False,False]},
                           {"title": "Seasonal Temperature for US Cities (April)<br> (Hover for City Info)"}]),
                dict(label="May",
                     method="update",
                     args=[{"visible": [False,False,False,False,True,False,False,False,False,False,False,False]},
                           {"title": "Seasonal Temperature for US Cities (May)<br> (Hover for City Info)"}]),
                dict(label="June",
                     method="update",
                     args=[{"visible": [False,False,False,False,False,True,False,False,False,False,False,False]},
                           {"title": "Seasonal Temperature for US Cities (June)<br> (Hover for City Info)"}]),
                dict(label="July",
                     method="update",
                     args=[{"visible": [False,False,False,False,False,False,True,False,False,False,False,False]},
                           {"title": "Seasonal Temperature for US Cities (July)<br> (Hover for City Info)"}]),
                dict(label="August",
                     method="update",
                     args=[{"visible": [False,False,False,False,False,False,False,True,False,False,False,False]},
                           {"title": "Seasonal Temperature for US Cities (August)<br> (Hover for City Info)"}]),
                dict(label="September",
                     method="update",
                     args=[{"visible": [False,False,False,False,False,False,False,False,True,False,False,False]},
                           {"title": "Seasonal Temperature for US Cities (September)<br> (Hover for City Info)"}]),
                dict(label="October",
                     method="update",
                     args=[{"visible": [False,False,False,False,False,False,False,False,False,True,False,False]},
                           {"title": "Seasonal Temperature for US Cities (October)<br> (Hover for City Info)"}]),
                dict(label="November",
                     method="update",
                     args=[{"visible": [False,False,False,False,False,False,False,False,False,False,True,False]},
                           {"title": "Seasonal Temperature for US Cities (November)<br> (Hover for City Info)"}]),
                dict(label="December",
                     method="update",
                     args=[{"visible": [False,False,False,False,False,False,False,False,False,False,False,True]},
                           {"title": "Seasonal Temperature for US Cities (December)<br> (Hover for City Info)"}]),   
            ]),
        )
    ])


    

html3 = fig.to_html()
fig.show()

In [151]:
html_string = html1 +"\n" + html2  +"\n" + html3  


with open("BP Charts.html", "w") as file:
    file.write(html_string)